In [4]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np

from tqdm import tqdm_notebook
import itertools

from tqdm import tqdm
from functools import partial

import pymorphy2

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.chrome.webdriver import WebDriver
from selenium.webdriver.chrome.options import Options

# from queue import Queue
from multiprocessing.dummy import Pool as ThreadPool
import multiprocessing
import concurrent.futures

from urllib.request import urlopen

from requests_html import HTMLSession

from typing import Dict, List

import threading
import warnings
import time

warnings.filterwarnings('ignore')

In [2]:
options = Options()
options.add_argument('--disable-blink-features=AutomationControlled')

In [3]:
URL = 'https://profi.ru/repetitor/english/?seamless=1&tabName=PROFILES'

In [ ]:
driver = webdriver.Chrome()
driver.get(URL)
html = driver.page_source
soup = BeautifulSoup(html, 'lxml')
repetitors = soup.find_all('div',
                           {'class': 'seamless-profile desktop-profile'})

## Сбор данных (вариант с генератором и удалением супов)

In [ ]:
def condition_one(status_text: List[BeautifulSoup]) -> str:
    """
    Проверка на отсутствие данных 
    :param status_text: список элементов статуса
    :return: текст статуса или "Статуса нет", если данных нет

    """
    if len(status_text) >= 2:
        second_status_element = status_text[1]
        status_text = second_status_element.get_text(strip=True)
        return status_text
    else:
        return "Статуса нет"


def condition_two(information: Tag) -> str:
    """
    Проверка на отсутствие данных
    :param information: информация по объекту
    :return: 'Нет', если информации нет, иначе текст информации
    """
    return 'Нет' if information is None else information


def external_data_collection(soup: BeautifulSoup) -> dict:
    """
    Вызов функций по сбору данных без входа в карточку и 
    преобразование результата в словарь
    :param soup: страница с данными репетитора
    :return: словарь с собранными данными
    """
    tutor_data = {}

    tutor_data["name"] = soup.find(
        'h1', {
            'class': 'ui_2MYaG ui_2SXfw ui_RF7aD ui_3owa1'
        }).text
    tutor_data["mark"] = soup.find(
        'span', {
            'data-shmid': 'profileIndicators_ratingBlock'
        }).text

    status_text = soup.find_all('div', {'class': 'ui_jKnqN'})
    status_text = condition_one(status_text)
    tutor_data["status"] = status_text

    tutor_data["passport"] = soup.find('span', {
        'data-shmid': 'profile_pinf'
    }).text

    attestation = soup.find('span', {
        'class':
        'ui-text sft-info-title _1JCcbzP _1i2s3kL _2iyzK60 _3YppjWm'
    })
    attestation = condition_two(attestation)
    tutor_data["attestation"] = attestation

    discount = soup.find('div', {'data-shmid': 'profile_discount-block'})
    discount = condition_two(discount)
    tutor_data["discount"] = discount

    tutor_data["price"] = soup.find('td', {
        'class': 'item_value'
    }).text.split('₽')[0]

    #     duration = soup.find('span', {'class':'ui-text price-list__duration _3xKhc83 _5DgZvLV'}).text.split('— ')[1]
    duration = soup.find(
        'span', {'class': 'ui-text price-list__duration _3xKhc83 _5DgZvLV'})
    duration = condition_two(duration)
    tutor_data["duration"] = duration

    location = soup.find_all(
        'div', {'class': 'ui-text _1Jx20En _3xKhc83 _2iyzK60 _3YppjWm'})
    location = condition_two(location)
    tutor_data["location"] = location

    return tutor_data

In [ ]:
def search_services(soup: BeautifulSoup, driver: WebDriver) -> list:
    """
    Поиск в собранных данных инф-ии об услугах и ценах
    :param soup: страница с данными репетитора
    :param driver: объект WebDriver для взаимодействия с браузером
    :return: список найденных услуг и цен
    """
    serv2 = 'Нет'
    amount = soup.find('span', {'class': 'ui-text _3xKhc83 _3QMH9Cr'})
    if amount == None:
        serv1 = soup.find('table',
                          {'class': 'price-list desktop-profile__prices'})
        serv2 = serv1.find_all('td', {'class': 'item_name item_name-bold'})
        serv_final = edit_text(serv2)
    else:
        try:
            time.sleep(2)
            button = WebDriverWait(driver, 3).until(
                EC.visibility_of_element_located(
                    (By.XPATH, "//*[@id='prices']/div/div/a/span")))
            button.click()
            WebDriverWait(driver, 3).until(EC.staleness_of(button))
            html2 = driver.page_source
            soup2 = BeautifulSoup(html2, 'lxml')
            serv1 = soup2.find_all(
                'table', {'class': 'price-list desktop-profile__prices'})[1]
            serv2 = serv1.find_all('td', {'class': 'item_name item_name-bold'})
            serv_final = edit_text(serv2)
        except:
            return serv2

    return serv_final


def edit_text(serv2: ResultSet) -> list:
    """
    Удаление лишней информации 
    :param serv2: набор результатов поиска, содержащий информацию об услугах
    :return: список отредактированных строк с информацией об услугах
    """
    servs = []
    for j in serv2:
        j = str(j).replace(
            '<td class="item_name item_name-bold"><span>',
            '').replace('</span><br/></td>', '').replace(
                '</span><br/><span class="ui-text _3eH689t _3QMH9Cr">', '')
        servs.append(j)
    return servs

In [ ]:
def clicker_func() -> list:
    """
    Нажатие на кнопку "Показать ещё" и вызов функции с генератором
    :return: список результатов после нажатия кнопки и сбора данных
    """
    driver = webdriver.Chrome()
    driver.get(URL)
    counter = 0
    try:
        while counter <= 150:
            # Прокручиваем страницу до конца
            driver.execute_script(
                "window.scrollTo(0, document.body.scrollHeight);")
            # Пауза, чтобы страница успела прогрузиться
            time.sleep(3)
            button = WebDriverWait(driver, 5).until(
                EC.visibility_of_element_located((
                    By.XPATH,
                    "//*[@id='page']/div/main/div/div/div[2]/div[2]/div/button"
                )))
            button.click()
            time.sleep(3)
            counter += 1
            WebDriverWait(driver, 5).until(EC.staleness_of(button))
    except:
        print(counter)

    html = driver.page_source
    soup = BeautifulSoup(html, 'lxml')
    repetitors = soup.find_all('div',
                               {'class': 'seamless-profile desktop-profile'})

    result = process_rep(repetitors, driver)
    #     driver.quit()
    return result


def process_rep(repetitors: List[BeautifulSoup], driver: WebDriver) -> list:
    """
    Создание генератора и добавление результата в список
    :param repetitors: список объектов BeautifulSoup (страницы с данными)
    :param driver: объект WebDriver 
    :return: список с результатом для каждого репетитора
    """
    options = Options()
    options.add_argument('--disable-blink-features=AutomationControlled')
    results = []
    # Генератор, который будет возвращать результат для каждого rep
    data_generator = (internal_data_collection(rep, driver)
                      for rep in repetitors)

    for data in data_generator:
        results.append(data)

    return results


def internal_data_collection(rep: Tag, driver: WebDriver) -> Dict[str, list]:
    """
    Вызов функций по сбору данных внутри карточки и 
    преобразование результата в словарь
    :param rep: информация о конкретном репетиторе
    :param driver: объект WebDriver
    :return: словарь с собранными данными о репетиторе
    """

    first_func = tutor_card(rep, driver)

    second_func = rate_info(first_func)

    third_func = basic_info(first_func)

    fourth_func = search_services(first_func, driver)

    fifth_func = external_data_collection(first_func)

    del first_func

    return {
        'rate_list': second_func,
        'basic_inf_list': third_func,
        'services_list': fourth_func,
        'general_inf_list': fifth_func
    }


def tutor_card(rep: Tag, driver: WebDriver) -> BeautifulSoup:
    """
    Сбор всех данных из карточки репетитора
    :param rep: информация о конкретном репетиторе
    :param driver: объект WebDriver 
    :return: страница репетитора
    """
    names_url = rep.find('a', {
        'class': 'ui_1hi7c ui_RF7aD ui_3j-OD'
    }).get("href")
    url = "https://profi.ru{}".format(names_url)
    driver.get(url)
    html = driver.page_source
    soup = BeautifulSoup(html, 'lxml')
    return soup


def rate_info(soup: BeautifulSoup) -> ResultSet:
    """
    Поиск в собранных данных информации об отзывах
    :param soup: страница с данными репетитора
    :return: текст с информацией об отзывах 
    """
    all_rates = soup.find_all('div', {'class': '_lWApzmR'})
    return all_rates


def basic_info(soup: BeautifulSoup) -> str:
    """
    Поиск в собранных данных инф-ии об образовании и опыте
    :param soup: Объект BeautifulSoup, представляющий страницу с данными
    :return: текст с информацией об образовании и опыте
    """
    all_info = soup.find('div', {'data-shmid': 'profileOIO'}).text
    return all_info

In [39]:
parse_results = clicker_func()

In [40]:
parse_results

[{'rate_list': [<div class="_lWApzmR">278</div>,
   <div class="_lWApzmR">21</div>,
   <div class="_lWApzmR">2</div>,
   <div class="_lWApzmR">1</div>,
   <div class="_lWApzmR">1</div>],
  'basic_inf_list': 'ОбразованиеUniversity of Saint Andrews (Великобритания), BSc in Economics2010 г.Подтверждено\xa0документомMSc in Finance2013 г.Подтверждено\xa0документомСертификат CELTA, Cambridge English2016 г.Подтверждено\xa0документомУниверситет Торонто Скарборо, физикас 2020 г. (3 года)Подтверждено\xa0документомУниверситет Саскачевана, компьютерные наукис 2020 г. (3 года)Подтверждено\xa0документомОпытСтаж репетиторствас 2011 г. (12 лет)Подтверждено\xa0документомПреподавал бизнес-английский корпоративным клиентамПодтверждено\xa0документомНа сервисе с июля 2015 г. (8 лет)Подтверждено\xa0ПрофиДополнительная информацияНоситель английского языка. гражданин ( Канада )с 2023 г.Носитель английского языка (Великобритания)',
  'services_list': ['Английский язык',
   'IELTS',
   'IELTS Academic',
   'IEL

In [41]:
len(parse_results)

1997

## Сохраняем в DataFrame

In [42]:
variable1 = []
variable2 = []
variable3 = []
variable4 = []

for pr in parse_results:
    rate_list = pr.get('rate_list')
    basic_inf_list = pr.get('basic_inf_list')
    services_list = pr.get('services_list')
    general_inf_list = pr.get('general_inf_list')

    variable1.append({'rate_list': rate_list})
    variable2.append({'basic_inf_list': basic_inf_list})
    variable3.append({'services_list': services_list})
    variable4.append({'general_inf_list': general_inf_list})

In [43]:
variable4

[{'general_inf_list': {'name': 'Emil Mekhriev',
   'mark': '4,89',
   'status': 'Очень хвалят',
   'passport': 'Паспорт проверен',
   'attestation': <span class="ui-text sft-info-title _1JCcbzP _1i2s3kL _2iyzK60 _3YppjWm">Уровень знаний подтверждён</span>,
   'discount': 'Нет',
   'price': '2940\xa0',
   'duration': <span class="ui-text price-list__duration _3xKhc83 _5DgZvLV">Длительность занятия — <!-- -->50<!-- --> мин.</span>,
   'location': [<div class="ui-text _1Jx20En _3xKhc83 _2iyzK60 _3YppjWm">Принимает у себя</div>,
    <div class="ui-text _1Jx20En _3xKhc83 _2iyzK60 _3YppjWm">Выезд к клиенту</div>,
    <div class="ui-text _1Jx20En _3xKhc83 _2iyzK60 _3YppjWm">Работает дистанционно</div>]}},
 {'general_inf_list': {'name': 'Ирина Юрьевна Попенкова',
   'mark': '4,85',
   'status': 'Очень хвалят',
   'passport': 'Паспорт проверен',
   'attestation': <span class="ui-text sft-info-title _1JCcbzP _1i2s3kL _2iyzK60 _3YppjWm">Уровень знаний подтверждён</span>,
   'discount': 'Нет',
   

In [154]:
# Извлекаем словари general_inf_list из каждого элемента списка
general_information = [item['general_inf_list'] for item in variable4]
df = pd.DataFrame(general_information)

### Первоначальное редактирование 

In [105]:
df1 = df.copy()

In [48]:
df2 = pd.DataFrame(
    columns=['5 stars', '4 stars', '3 stars', '2 stars', '1 stars'])

# Проходим по каждому элементу списка и заменяем значения
for index, item in enumerate(variable1):
    rate_list = item['rate_list']
    rate_list = [int(div.get_text(strip=True)) for div in rate_list]
    df2.loc[index] = rate_list

In [107]:
# Добавление пустых колонок для каждого элемента rate_list
for i in range(5):
    df1[f'{i + 1}_stars'] = None

for i, item in enumerate(variable1):
    for j, value in enumerate(item['rate_list']):
        df1.at[i, f'{5 - j}_stars'] = int(value.text)

In [ ]:
for col in df1['attestation']:
    df1['attestation'] = df1['attestation'].apply(lambda x: x.text
                                                  if x != 'Нет' else x)

In [139]:
for col in df1['duration']:
    df1['duration'] = df1['duration'].apply(lambda x: x.split(' мин')[0]
                                            if x != 'Нет' else x)

In [148]:
def edit_location(locations: ResultSet) -> list:
    """
    Редактирование данных
    :param locations: данные о месте проведения занятия
    :return: обновленный список с местом проведения занятия
    """
    return [
        location.text if location != 'Нет' else location
        for location in locations
    ]


df1['location'] = df1['location'].apply(edit_location)

In [ ]:
df1['Teaches_at_home'] = 0
df1['Teaches_at_clients_place'] = 0
df1['Teaches_remotely'] = 0


def set_values(row: pd.Series):
    """
    Установка значений в новых столбцах на основе признака location
    :param locations: данные о месте проведения занятия
    :return: обновленный список с местом проведения занятия
    """
    if 'Принимает у себя' in row['location']:
        row['Teaches_at_home'] = 1
    if 'Выезд к клиенту' in row['location']:
        row['Teaches_at_clients_place'] = 1
    if 'Работает дистанционно' in row['location']:
        row['Teaches_remotely'] = 1
    return row


df1 = df1.apply(set_values, axis=1)

In [161]:
df1.drop('location', axis=1, inplace=True)

### Поиск ключевых слов

In [ ]:
def check_keywords(list_of_dicts: list, keywords: List[str]) -> dict:
    """
    Поиск ключевых слов для basic info
    :param list_of_dicts: инф-ия об образовании и опыте со страницы репетитора 
    :param keywords: список ключевых слов для поиска в тексте 
    :return: 
    """
    results = {keyword: [] for keyword in keywords}

    for text_dict in list_of_dicts:
        text = text_dict['basic_inf_list']  # Получаем текст из словаря
        keyword_found = {keyword: 0 for keyword in keywords}

        for keyword in keywords:
            if keyword.lower() in text.lower():
                keyword_found[keyword] = 1

        for keyword, found in keyword_found.items():
            results[keyword].append(found)

    return results


def load_keywords_from_file(file_path: str) -> list:
    """
    Загрузка ключевых слов из файла
    :param file_path: путь до файла с ключевыми словами
    :return: список ключевых слов
    """
    keywords = []

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            keyword = line.strip()
            if keyword:
                keywords.append(keyword)

    return keywords


file_path = 'keywords_for_basic_inf.txt'

input_keywords = load_keywords_from_file(file_path)

results = check_keywords(variable2, input_keywords)

In [173]:
new_columns = list(results.keys())

for col_name, col_data in results.items():
    df1[col_name] = col_data

In [179]:
def check_keywords2(list_of_dicts: list, keywords: str) -> list:
    """
    Поиск ключевых слов для services
    :param list_of_dicts: инф-ия об об услугах и ценах со страницы репетитора 
    :param keywords: список ключевых слов для поиска в тексте 
    :return: 
    """
    results = {keyword: [] for keyword in keywords}

    for text_dict in list_of_dicts:
        # Получаем список строк из словаря
        text_list = text_dict['services_list']
        keyword_found = {keyword: 0 for keyword in keywords}

        for keyword in keywords:
            for text in text_list:
                if keyword.lower() in text.lower():
                    keyword_found[keyword] = 1
                    break  # Если нашли хотя бы один раз, переходим к следующему ключевому слову

        for keyword, found in keyword_found.items():
            results[keyword].append(found)

    return results


file_path = 'keywords_for_services.txt'

input_keywords2 = load_keywords_from_file(file_path)

results = check_keywords2(variable3, input_keywords2)

In [183]:
new_columns = list(results.keys())

for col_name, col_data in results.items():
    df1[col_name] = col_data

In [186]:
df1

name  mark        status          passport  \
0                         Emil Mekhriev  4,89  Очень хвалят  Паспорт проверен   
1               Ирина Юрьевна Попенкова  4,85  Очень хвалят  Паспорт проверен   
2           Александр Юрьевич Иванченко  4,95  Очень хвалят  Паспорт проверен   
3             Максим Станиславович Юдин  4,95  Очень хвалят  Паспорт проверен   
4             Светлана Андреевна Орлова  4,99  Очень хвалят  Паспорт проверен   
...                                 ...   ...           ...               ...   
1992      Наталья Григорьевна Трегубова  4,93  Очень хвалят  Паспорт проверен   
1993    Диана Александровна Гапсаламова  4,75   Статуса нет  Паспорт проверен   
1994       Татьяна Владимировна Олийник  4,86   Статуса нет  Паспорт проверен   
1995  Екатерина Александровна Субботина  4,85   Статуса нет  Паспорт проверен   
1996       Дмитрий Анатольевич Микрюков  4,93   Статуса нет  Паспорт проверен   

                     attestation discount       price    duration  1_stars  \
0     Уровень знаний подтверждён      Нет       2940           50        1   
1     Уровень знаний подтверждён      Нет  1600–2000        60–90        0   
2     Уровень знаний подтверждён      Нет       2200        60–90        1   
3                            Нет     Есть  2990–4000           60        1   
4     Уровень знаний подтверждён     Есть       4000           60        0   
...                          ...      ...         ...         ...      ...   
1992                         Нет     Есть       2000   по запросу        0   
1993                         Нет      Нет  1500–2000           60        0   
1994                         Нет      Нет  1000–1500           60        0   
1995                         Нет      Нет   900–1400        60–90        0   
1996  Уровень знаний подтверждён      Нет       1070           90        0   

      2_stars  ...  Английский для путешествий  ОГЭ по английскому языку  ОГЭ  \
0           1  ...                           1                         1    1   
1           3  ...                           0                         1    1   
2           0  ...                           0                         1    1   
3           3  ...                           1                         1    1   
4           0  ...                           1                         1    1   
...       ...  ...                         ...                       ...  ...   
1992        0  ...                           1                         0    0   
1993        0  ...                           0                         0    1   
1994        0  ...                           0                         1    1   
1995        0  ...                           0                         0    0   
1996        0  ...                           1                         1    1   

      Английский для дошкольников  Американский английский язык  \
0                               1                             1   
1                               0                             0   
2                               0                             0   
3                               0                             1   
4                               0                             0   
...                           ...                           ...   
1992                            0                             0   
1993                            0                             0   
1994                            0                             0   
1995                            0                             0   
1996                            0                             0   

      Британский английский язык  Олимпиады по английскому языку  \
0                              1                               1   
1                              0                               0   
2                              0                               0   
3                              1                               1   
4      

In [8]:
# сохраняем в csv
df1.to_csv('../data/parse1997.csv', index=False)